In [1]:
######
#neural net example
from __future__ import print_function
from __future__ import division
import torch
import torch.nn as nn
import torch.optim as optim
import numpy as np
import torchvision
from torchvision import datasets, models, transforms
import matplotlib.pyplot as plt
import time
import os
import copy
print("PyTorch Version: ",torch.__version__)
print("Torchvision Version: ",torchvision.__version__)

PyTorch Version:  1.0.1.post2
Torchvision Version:  0.2.1


In [3]:
# Top level data directory. Here we assume the format of the directory conforms
#   to the ImageFolder structure
#note that the training set of data should be in a folder called train
#the validation set data should be in a folder called val. inside
# train and val there should be two folders named after
# our classes. One called alcoholic with the alcoholics data and control with control
# data. ImageFolder loader will automatically assign and keep track of labels.
#will automatically assign labels
data_dir = "/Users/chvillal/Documents/GitHub/EEG_Alcoholism_Classification/Data/images"

# Models to choose from [resnet, alexnet, vgg, squeezenet, densenet, inception]
model_name = "inception"

# Number of classes in the dataset
num_classes = 2

# Batch size for training (change depending on how much memory you have)
batch_size = 5

# Number of epochs to train for
num_epochs = 15

# Flag for feature extracting. When False, we finetune the whole model,
#   when True we only update the reshaped layer params
feature_extract = False

In [4]:
def train_model(model, dataloaders, criterion, optimizer, num_epochs=25, is_inception=False):
    since = time.time()

    val_acc_history = []

    best_model_wts = copy.deepcopy(model.state_dict())
    best_acc = 0.0

    for epoch in range(num_epochs):
        print('Epoch {}/{}'.format(epoch, num_epochs - 1))
        print('-' * 10)

        # Each epoch has a training and validation phase
        for phase in ['train', 'val']:
            if phase == 'train':
                model.train()  # Set model to training mode
            else:
                model.eval()   # Set model to evaluate mode

            running_loss = 0.0
            running_corrects = 0

            # Iterate over data.
            for inputs, labels in dataloaders[phase]:
                inputs = inputs.to(device)
                labels = labels.to(device)

                # zero the parameter gradients
                optimizer.zero_grad()

                # forward
                # track history if only in train
                with torch.set_grad_enabled(phase == 'train'):
                    # Get model outputs and calculate loss
                    # Special case for inception because in training it has an auxiliary output. In train
                    #   mode we calculate the loss by summing the final output and the auxiliary output
                    #   but in testing we only consider the final output.
                    if is_inception and phase == 'train':
                        # From https://discuss.pytorch.org/t/how-to-optimize-inception-model-with-auxiliary-classifiers/7958
                        outputs, aux_outputs = model(inputs)
                        loss1 = criterion(outputs, labels)
                        loss2 = criterion(aux_outputs, labels)
                        loss = loss1 + 0.4*loss2
                    else:
                        outputs = model(inputs)
                        loss = criterion(outputs, labels)

                    _, preds = torch.max(outputs, 1)

                    # backward + optimize only if in training phase
                    if phase == 'train':
                        loss.backward()
                        optimizer.step()

                # statistics
                running_loss += loss.item() * inputs.size(0)
                running_corrects += torch.sum(preds == labels.data)

            epoch_loss = running_loss / len(dataloaders[phase].dataset)
            epoch_acc = running_corrects.double() / len(dataloaders[phase].dataset)

            print('{} Loss: {:.4f} Acc: {:.4f}'.format(phase, epoch_loss, epoch_acc))

            # deep copy the model
            if phase == 'val' and epoch_acc > best_acc:
                best_acc = epoch_acc
                best_model_wts = copy.deepcopy(model.state_dict())
            if phase == 'val':
                val_acc_history.append(epoch_acc)

        print()

    time_elapsed = time.time() - since
    print('Training complete in {:.0f}m {:.0f}s'.format(time_elapsed // 60, time_elapsed % 60))
    print('Best val Acc: {:4f}'.format(best_acc))

    # load best model weights
    model.load_state_dict(best_model_wts)
    return model, val_acc_history

In [5]:
def set_parameter_requires_grad(model, feature_extracting):
    if feature_extracting:
        for param in model.parameters():
            param.requires_grad = False

In [6]:
def initialize_model(model_name, num_classes, feature_extract, use_pretrained=False):
    # Initialize these variables which will be set in this if statement. Each of these
    #   variables is model specific.
    model_ft = None
    input_size = 0

    if model_name == "resnet":
        """ Resnet18
        """
        model_ft = models.resnet18(pretrained=use_pretrained)
        set_parameter_requires_grad(model_ft, feature_extract)
        num_ftrs = model_ft.fc.in_features
        model_ft.fc = nn.Linear(num_ftrs, num_classes)
        input_size = 224

    elif model_name == "alexnet":
        """ Alexnet
        """
        model_ft = models.alexnet(pretrained=use_pretrained)
        set_parameter_requires_grad(model_ft, feature_extract)
        num_ftrs = model_ft.classifier[6].in_features
        model_ft.classifier[6] = nn.Linear(num_ftrs,num_classes)
        input_size = 224

    elif model_name == "vgg":
        """ VGG11_bn
        """
        model_ft = models.vgg11_bn(pretrained=use_pretrained)
        set_parameter_requires_grad(model_ft, feature_extract)
        num_ftrs = model_ft.classifier[6].in_features
        model_ft.classifier[6] = nn.Linear(num_ftrs,num_classes)
        input_size = 224

    elif model_name == "squeezenet":
        """ Squeezenet
        """
        model_ft = models.squeezenet1_0(pretrained=use_pretrained)
        set_parameter_requires_grad(model_ft, feature_extract)
        model_ft.classifier[1] = nn.Conv2d(512, num_classes, kernel_size=(1,1), stride=(1,1))
        model_ft.num_classes = num_classes
        input_size = 224

    elif model_name == "densenet":
        """ Densenet
        """
        model_ft = models.densenet121(pretrained=use_pretrained)
        set_parameter_requires_grad(model_ft, feature_extract)
        num_ftrs = model_ft.classifier.in_features
        model_ft.classifier = nn.Linear(num_ftrs, num_classes)
        input_size = 224

    elif model_name == "inception":
        """ Inception v3
        Be careful, expects (299,299) sized images and has auxiliary output
        """
        model_ft = models.inception_v3(pretrained=use_pretrained)
        set_parameter_requires_grad(model_ft, feature_extract)
        # Handle the auxilary net
        num_ftrs = model_ft.AuxLogits.fc.in_features
        model_ft.AuxLogits.fc = nn.Linear(num_ftrs, num_classes)
        # Handle the primary net
        num_ftrs = model_ft.fc.in_features
        model_ft.fc = nn.Linear(num_ftrs,num_classes)
        input_size = 299

    else:
        print("Invalid model name, exiting...")
        exit()

    return model_ft, input_size

In [7]:
def set_parameter_requires_grad(model, feature_extracting):
    if feature_extracting:
        for param in model.parameters():
            param.requires_grad = False

In [8]:

# Initialize the model for this run
model_ft, input_size = initialize_model(model_name, num_classes, feature_extract, use_pretrained=False)

# Print the model we just instantiated
print(model_ft)


Inception3(
  (Conv2d_1a_3x3): BasicConv2d(
    (conv): Conv2d(3, 32, kernel_size=(3, 3), stride=(2, 2), bias=False)
    (bn): BatchNorm2d(32, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_2a_3x3): BasicConv2d(
    (conv): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(32, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_2b_3x3): BasicConv2d(
    (conv): Conv2d(32, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
    (bn): BatchNorm2d(64, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_3b_1x1): BasicConv2d(
    (conv): Conv2d(64, 80, kernel_size=(1, 1), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(80, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_4a_3x3): BasicConv2d(
    (conv): Conv2d(80, 192, kernel_size=(3, 3), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(192, eps=0.001, momentum=0.1, affine=True, t

In [9]:
# Data augmentation and normalization for training
# Just normalization for validation
data_transforms = {
    'train': transforms.Compose([
        transforms.RandomResizedCrop(input_size),
        transforms.RandomHorizontalFlip(),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
    'val': transforms.Compose([
        transforms.Resize(input_size),
        transforms.CenterCrop(input_size),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
}

print("Initializing Datasets and Dataloaders...")

# Create training and validation datasets
image_datasets = {x: datasets.ImageFolder(os.path.join(data_dir, x), data_transforms[x]) for x in ['train', 'val']}
# Create training and validation dataloaders
dataloaders_dict = {x: torch.utils.data.DataLoader(image_datasets[x], batch_size=batch_size, shuffle=True, num_workers=4) for x in ['train', 'val']}
# Detect if we have a GPU available
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

Initializing Datasets and Dataloaders...


OSError: [Errno 2] No such file or directory: '/Users/chvillal/Documents/GitHub/EEG_Alcoholism_Classification/Data/images/train'

In [10]:
# Send the model to GPU
model_ft = model_ft.to(device)

# Gather the parameters to be optimized/updated in this run. If we are
#  finetuning we will be updating all parameters. However, if we are
#  doing feature extract method, we will only update the parameters
#  that we have just initialized, i.e. the parameters with requires_grad
#  is True.
params_to_update = model_ft.parameters()
print("Params to learn:")
if feature_extract:
    params_to_update = []
    for name,param in model_ft.named_parameters():
        if param.requires_grad == True:
            params_to_update.append(param)
            print("\t",name)
else:
    for name,param in model_ft.named_parameters():
        if param.requires_grad == True:
            print("\t",name)

# Observe that all parameters are being optimized
optimizer_ft = optim.SGD(params_to_update, lr=0.001, momentum=0.9)


Params to learn:
	 Conv2d_1a_3x3.conv.weight
	 Conv2d_1a_3x3.bn.weight
	 Conv2d_1a_3x3.bn.bias
	 Conv2d_2a_3x3.conv.weight
	 Conv2d_2a_3x3.bn.weight
	 Conv2d_2a_3x3.bn.bias
	 Conv2d_2b_3x3.conv.weight
	 Conv2d_2b_3x3.bn.weight
	 Conv2d_2b_3x3.bn.bias
	 Conv2d_3b_1x1.conv.weight
	 Conv2d_3b_1x1.bn.weight
	 Conv2d_3b_1x1.bn.bias
	 Conv2d_4a_3x3.conv.weight
	 Conv2d_4a_3x3.bn.weight
	 Conv2d_4a_3x3.bn.bias
	 Mixed_5b.branch1x1.conv.weight
	 Mixed_5b.branch1x1.bn.weight
	 Mixed_5b.branch1x1.bn.bias
	 Mixed_5b.branch5x5_1.conv.weight
	 Mixed_5b.branch5x5_1.bn.weight
	 Mixed_5b.branch5x5_1.bn.bias
	 Mixed_5b.branch5x5_2.conv.weight
	 Mixed_5b.branch5x5_2.bn.weight
	 Mixed_5b.branch5x5_2.bn.bias
	 Mixed_5b.branch3x3dbl_1.conv.weight
	 Mixed_5b.branch3x3dbl_1.bn.weight
	 Mixed_5b.branch3x3dbl_1.bn.bias
	 Mixed_5b.branch3x3dbl_2.conv.weight
	 Mixed_5b.branch3x3dbl_2.bn.weight
	 Mixed_5b.branch3x3dbl_2.bn.bias
	 Mixed_5b.branch3x3dbl_3.conv.weight
	 Mixed_5b.branch3x3dbl_3.bn.weight
	 Mixed_5b.b

In [11]:
###############################
#note that if model_ft, hist = train_model(...) crashes with
# try removing one image from the training set
#https://forums.fast.ai/t/understanding-code-error-expected-more-than-1-value-per-channel-when-training/9257/10
criterion = nn.CrossEntropyLoss()

# Train and evaluate
model_ft, hist = train_model(model_ft, dataloaders_dict, criterion, optimizer_ft, num_epochs=num_epochs, is_inception=(model_name=="inception"))

Epoch 0/14
----------
tensor([[[[ 1.7180,  1.8379,  2.0092,  ...,  1.9235,  2.0092,  2.0777],
          [ 1.7009,  1.8208,  2.0092,  ...,  2.0263,  2.0948,  2.1290],
          [ 1.6667,  1.8037,  1.9920,  ...,  2.2147,  2.2147,  2.2318],
          ...,
          [ 1.8379,  1.8893,  1.9407,  ...,  1.9578,  1.9235,  1.9064],
          [ 1.9407,  2.0263,  2.1290,  ...,  2.0263,  2.0263,  2.0263],
          [ 2.0092,  2.1119,  2.2489,  ...,  2.0777,  2.0948,  2.1119]],

         [[ 2.2185,  2.1835,  2.1134,  ..., -0.6702, -0.7052, -0.7227],
          [ 2.2185,  2.1835,  2.1134,  ..., -0.4251, -0.4601, -0.4776],
          [ 2.2185,  2.1660,  2.0959,  ...,  0.0126, -0.0224, -0.0399],
          ...,
          [ 1.0280,  0.8704,  0.6429,  ..., -1.3529, -1.4230, -1.4580],
          [ 0.5903,  0.5203,  0.4328,  ..., -1.4405, -1.4580, -1.4755],
          [ 0.3452,  0.3277,  0.2927,  ..., -1.4930, -1.4930, -1.4930]],

         [[-1.5779, -1.6650, -1.8044,  ..., -1.8044, -1.8044, -1.8044],
        

tensor([[[[ 1.9235,  2.2147,  2.2489,  ...,  0.5536,  0.3481,  0.0056],
          [ 1.9749,  2.2489,  2.2489,  ...,  0.3994,  0.2967,  0.2282],
          [ 1.9749,  2.2489,  2.2489,  ...,  0.7248,  0.8447,  0.4337],
          ...,
          [ 2.0948,  2.2489,  2.2489,  ..., -2.1179, -2.1179, -1.8782],
          [ 1.9749,  2.2318,  2.2489,  ..., -2.1179, -2.0665, -1.7412],
          [ 1.8550,  2.1290,  2.2489,  ..., -2.1179, -1.7240, -1.2103]],

         [[-1.4930, -1.6331, -1.7206,  ...,  2.2010,  2.3235,  2.4286],
          [-1.5105, -1.6331, -1.7031,  ...,  2.4111,  2.4111,  2.0959],
          [-1.5105, -1.6331, -1.7031,  ...,  2.4286,  2.4286,  1.9734],
          ...,
          [-1.5805, -1.7031, -1.7731,  ...,  2.4286,  2.4111,  2.0959],
          [-1.5280, -1.6681, -1.7206,  ...,  2.4286,  2.3235,  1.9209],
          [-1.4580, -1.5980, -1.6506,  ...,  2.4286,  2.3585,  2.0609]],

         [[-1.5953, -1.6650, -1.6824,  ..., -1.8044, -1.6476, -1.4559],
          [-1.6650, -1.7696, -

tensor([[[[ 2.2318,  2.2318,  2.2318,  ..., -1.6727, -1.7240, -1.7583],
          [ 2.2318,  2.2318,  2.2318,  ..., -1.5185, -1.5870, -1.6555],
          [ 2.2318,  2.2318,  2.2318,  ..., -1.2788, -1.3644, -1.4672],
          ...,
          [ 2.1975,  2.1975,  2.1975,  ..., -0.8507, -0.7822, -0.6965],
          [ 2.2489,  2.2489,  2.2489,  ...,  0.2111,  0.1254,  0.0912],
          [ 2.2489,  2.2489,  2.2489,  ...,  1.1187,  0.8789,  0.7248]],

         [[-1.6155, -1.6155, -1.6155,  ...,  2.3761,  2.4286,  2.4286],
          [-1.6155, -1.6155, -1.6155,  ...,  2.3761,  2.4286,  2.4286],
          [-1.6155, -1.6155, -1.6155,  ...,  2.3585,  2.4286,  2.4286],
          ...,
          [-1.6155, -1.6155, -1.6155,  ...,  2.4111,  2.4111,  2.4286],
          [-1.6681, -1.6681, -1.6681,  ...,  2.4286,  2.4286,  2.4286],
          [-1.7031, -1.7031, -1.7031,  ...,  2.4286,  2.4286,  2.4286]],

         [[-1.8044, -1.8044, -1.8044,  ..., -1.7173, -1.7696, -1.8044],
          [-1.8044, -1.8044, -

tensor([[[[ 2.2489,  2.2489,  2.2318,  ...,  2.0948,  2.1290,  2.1975],
          [ 2.2489,  2.2489,  2.2318,  ...,  2.0434,  2.0605,  2.1119],
          [ 2.2489,  2.2489,  2.2318,  ...,  1.9578,  1.9407,  1.9749],
          ...,
          [ 2.2489,  2.2489,  2.2318,  ...,  2.2489,  2.2318,  2.2147],
          [ 2.2489,  2.2489,  2.2318,  ...,  2.2147,  2.1975,  2.1975],
          [ 2.2489,  2.2489,  2.2318,  ...,  2.1975,  2.1804,  2.1804]],

         [[-1.7031, -1.6681, -1.6331,  ...,  0.5028,  0.3803,  0.2752],
          [-1.7031, -1.6681, -1.6331,  ...,  0.5553,  0.3803,  0.2402],
          [-1.7031, -1.6681, -1.6331,  ...,  0.6429,  0.3978,  0.1877],
          ...,
          [-1.7031, -1.6681, -1.6331,  ..., -0.7227, -0.6877, -0.6702],
          [-1.7031, -1.6681, -1.6331,  ..., -0.7052, -0.6702, -0.6352],
          [-1.7031, -1.6681, -1.6331,  ..., -0.6877, -0.6527, -0.6176]],

         [[-1.8044, -1.8044, -1.8044,  ..., -1.7173, -1.5779, -1.4559],
          [-1.8044, -1.8044, -

tensor([[[[ 0.7077,  0.7591,  0.9132,  ...,  2.2318,  2.2318,  2.2318],
          [ 0.2111,  0.2282,  0.3309,  ...,  2.2318,  2.2318,  2.2318],
          [-0.3198, -0.3541, -0.3369,  ...,  2.2318,  2.2318,  2.2318],
          ...,
          [ 2.2147,  2.2318,  2.2318,  ...,  2.2318,  2.2318,  2.2318],
          [ 2.2489,  2.2489,  2.2489,  ...,  2.2318,  2.2318,  2.2318],
          [ 2.2489,  2.2489,  2.2489,  ...,  2.2318,  2.2318,  2.2318]],

         [[ 2.3761,  2.3060,  2.2535,  ..., -1.6155, -1.6155, -1.6155],
          [ 2.4111,  2.3761,  2.3410,  ..., -1.6155, -1.6155, -1.6155],
          [ 2.4286,  2.4286,  2.3761,  ..., -1.6155, -1.6155, -1.6155],
          ...,
          [ 1.0455,  1.0455,  1.0630,  ..., -1.6155, -1.6155, -1.6155],
          [ 1.0805,  1.0455,  1.0630,  ..., -1.6155, -1.6155, -1.6155],
          [ 1.0980,  1.0630,  1.0630,  ..., -1.6155, -1.6155, -1.6155]],

         [[-1.8044, -1.8044, -1.8044,  ..., -1.8044, -1.8044, -1.8044],
          [-1.6476, -1.7173, -

...

tensor([[[[-1.1075, -0.3883,  0.5364,  ...,  1.8550,  1.5982,  1.2899],
          [ 0.0398, -0.3369,  0.0912,  ...,  1.9064,  1.6495,  1.3413],
          [ 1.4440,  0.3823, -0.2171,  ...,  1.9749,  1.7180,  1.4269],
          ...,
          [ 2.2489,  0.3309, -2.1179,  ...,  2.2489,  2.0263,  1.7009],
          [ 1.9064,  0.1597, -2.1179,  ...,  2.0605,  1.7865,  1.4783],
          [ 1.4098,  0.0227, -1.8097,  ...,  1.7694,  1.4783,  1.1529]],

         [[-1.3880, -1.3704, -1.4405,  ..., -1.5280, -1.4055, -1.2479],
          [-1.2479, -2.0007, -2.0182,  ..., -1.5455, -1.4230, -1.2654],
          [-1.5805, -2.0357, -2.0357,  ..., -1.5805, -1.4580, -1.3179],
          ...,
          [-1.8081, -1.8606, -1.7206,  ..., -1.6331, -1.5280, -1.4055],
          [-1.6155, -1.7381, -1.8431,  ..., -1.5805, -1.4755, -1.3529],
          [-1.4055, -1.5980, -1.9132,  ..., -1.4930, -1.3704, -1.2479]],

         [[ 0.2871,  1.2980,  1.9777,  ..., -1.5953, -1.5430, -1.4733],
          [ 1.3677,  1.8034,  

tensor([[[[ 1.9235,  1.1187, -2.1179,  ...,  1.8550,  1.5982,  1.2899],
          [ 1.6324,  1.7865,  0.2967,  ...,  1.9064,  1.6495,  1.3413],
          [ 1.3413,  2.2489,  2.2489,  ...,  1.9749,  1.7180,  1.4269],
          ...,
          [ 2.0948,  2.1633,  1.4440,  ...,  2.2489,  2.0263,  1.7009],
          [ 2.0434,  2.2318,  1.7352,  ...,  2.0605,  1.7865,  1.4783],
          [ 1.7865,  1.9920,  1.5810,  ...,  1.7694,  1.4783,  1.1529]],

         [[-2.0357, -1.0903, -1.5105,  ..., -1.5280, -1.4055, -1.2479],
          [-2.0007, -1.5805, -1.6506,  ..., -1.5455, -1.4230, -1.2654],
          [-1.8782, -1.8606, -1.9832,  ..., -1.5805, -1.4580, -1.3179],
          ...,
          [-1.8957, -2.0357, -1.8431,  ..., -1.6331, -1.5280, -1.4055],
          [-1.8782, -2.0357, -1.9307,  ..., -1.5805, -1.4755, -1.3529],
          [-1.7906, -1.7731, -1.8256,  ..., -1.4930, -1.3704, -1.2479]],

         [[ 0.6008,  1.5594,  0.2348,  ..., -1.5953, -1.5430, -1.4733],
          [-0.3578,  1.1585,  

tensor([[[[ 2.2489,  0.0741, -2.1179,  ...,  1.8550,  1.5982,  1.2899],
          [ 0.8276, -2.1179, -1.6384,  ...,  1.9064,  1.6495,  1.3413],
          [-1.9638, -1.7754, -2.1179,  ...,  1.9749,  1.7180,  1.4269],
          ...,
          [-2.1179, -2.1179, -2.1179,  ...,  2.2489,  2.0263,  1.7009],
          [-2.1179, -2.1179, -2.1179,  ...,  2.0605,  1.7865,  1.4783],
          [-1.3644, -1.7069, -1.9980,  ...,  1.7694,  1.4783,  1.1529]],

         [[-2.0357, -1.9657, -0.6702,  ..., -1.5280, -1.4055, -1.2479],
          [-1.8256, -1.7031,  2.1485,  ..., -1.5455, -1.4230, -1.2654],
          [-1.1078,  1.7808,  2.4286,  ..., -1.5805, -1.4580, -1.3179],
          ...,
          [ 0.2227,  0.7304,  1.2731,  ..., -1.6331, -1.5280, -1.4055],
          [ 1.6758,  2.0434,  2.2185,  ..., -1.5805, -1.4755, -1.3529],
          [ 2.0959,  2.4111,  2.4286,  ..., -1.4930, -1.3704, -1.2479]],

         [[ 1.8557,  2.5877,  1.9777,  ..., -1.5953, -1.5430, -1.4733],
          [ 1.8557,  0.7228,  

tensor([[[[ 1.7352,  0.9303,  0.4508,  ...,  1.8550,  1.5982,  1.2899],
          [ 1.0159,  0.3138, -1.6042,  ...,  1.9064,  1.6495,  1.3413],
          [-0.6794, -1.5014, -1.6727,  ...,  1.9749,  1.7180,  1.4269],
          ...,
          [ 2.2489,  0.1768, -2.1179,  ...,  2.2489,  2.0263,  1.7009],
          [ 2.2489,  0.4851, -2.1179,  ...,  2.0605,  1.7865,  1.4783],
          [ 2.2489,  0.2453, -1.8610,  ...,  1.7694,  1.4783,  1.1529]],

         [[-1.3354, -1.6331, -1.4055,  ..., -1.5280, -1.4055, -1.2479],
          [-1.7381, -1.1429, -1.4755,  ..., -1.5455, -1.4230, -1.2654],
          [-2.0357, -1.1429,  0.7129,  ..., -1.5805, -1.4580, -1.3179],
          ...,
          [-2.0357, -1.5805, -0.5826,  ..., -1.6331, -1.5280, -1.4055],
          [-2.0357, -1.6681, -0.3550,  ..., -1.5805, -1.4755, -1.3529],
          [-2.0357, -1.5455, -0.2325,  ..., -1.4930, -1.3704, -1.2479]],

         [[-0.3404,  0.6531,  2.4657,  ..., -1.5953, -1.5430, -1.4733],
          [ 1.7685,  2.2391,  

val Loss: 0.7512 Acc: 0.6667

Training complete in 58m 12s
Best val Acc: 0.807018
